In [1]:
import pandas as pd
import useful_functions as use
from fuzzywuzzy import fuzz
import usaddress
from datetime import datetime, date
from dateutil.relativedelta import relativedelta

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
ppd = use.get_ppd()

C:/Users/vigrose/Data/PPD\ppd_data_20210612.csv


C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3249: DtypeWarning: Columns (13,14,20,21,42,49,56,57,72) have mixed types. Specify dtype option on import or set low_memory=False.
  if (await self.run_code(code, result,  async_=asy)):


In [12]:
datagov = pd.read_csv('../../Data/DataGov/All_Data_210617.csv')
# cred = pd.read_csv('../../Data/Credentialling/Credentialing_Addresses_2021-06-16.csv')
# ppd = ppd.fillna('None')
datagov = datagov.fillna('None')
# cred = cred.fillna('None')

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3058: DtypeWarning: Columns (8,9,10) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [13]:
# cred['ME'] = use.fix_me(cred.ME)
datagov['ME'] = use.fix_me(datagov.ME)
# ppd['ME'] = use.fix_me(ppd.ME)

In [5]:
cred['FULL_DT'] = pd.to_datetime(cred.FULL_DT)

In [14]:
gov = datagov[datagov.phn_numbr!='None']

In [7]:
today_date = datetime.today()
six_months_ago  = today_date - relativedelta(months=6)

In [8]:
full = 4915513
reapp = 4915514
keeps = []
for row in cred.itertuples():
    if row.ORDER_PRODUCT_ID == reapp:
        keep = True
    elif row.ORDER_PRODUCT_ID == full and row.FULL_DT > six_months_ago:
        keep = True
    else:
        keep = False
    keeps.append(keep)

In [9]:
good_cred = cred[keeps]
good_cred = good_cred.sort_values('FULL_DT')

In [17]:
good_cred.head()

ORG_ID                                    ORG_NAME PARTY_ID_x  STATUS  \
113758    3588  Owensboro Health Twin Lakes Medical Center       None       1   
444247    2202    Borland Groover Clinic, PA Credentialing       None       1   
444252    2202    Borland Groover Clinic, PA Credentialing       None       1   
444256    2202    Borland Groover Clinic, PA Credentialing       None       1   
444257    2202    Borland Groover Clinic, PA Credentialing       None       1   

        ADVANTAGE_ID    ADDRESS_LINE_1 ADDRESS_LINE_2          CITY STATE  \
113758       2086041   910 Wallace Ave           None   Leitchfield    KY   
444247       2083968  4800 Belfort Rd.           None  Jacksonville    FL   
444252       2083968  4800 Belfort Rd.           None  Jacksonville    FL   
444256       2083968  4800 Belfort Rd.           None  Jacksonville    FL   
444257       2083968  4800 Belfort Rd.           None  Jacksonville    FL   

          ZIPCODE  ... PARTY_ID_y ORDER_NBR  ORDER_PRODUCT_ID  \
113758  427542414  ...    3462804  41781619           4915514   
444247      32256  ...    2860558  41781261           4915514   
444252      32256  ...    3378444  41781261           4915514   
444256      32256  ...    1838955  41781261           4915514   
444257      32256  ...    2170576  41781261           4915514   

       ORDER_PHYSICIAN_HIST_KEY CUSTOMER_KEY  CUSTOMER_ISELL_LOGIN  \
113758                  5945790        57630             20HP10137   
444247                  5812576        58016             11AM64555   
444252                  5888521        58016             11AM64555   
444256                  6407780        58016             11AM64555   
444257                  6504408        58016             11AM64555   

                                   CUSTOMER_NAME          CUSTOMER_TYPE_DESC  \
113758        Twin Lakes Regional Medical Center  Eprofile Webstore Customer   
444247  Borland Groover Clinic, Pa Credentialing  Eprofile Webstore Customer   
444252  Borland Groover Clinic, Pa Credentialing  Eprofile Webstore Customer   
444256  Borland Groover Clinic, Pa Credentialing  Eprofile Webstore Customer   
444257  Borland Groover Clinic, Pa Credentialing  Eprofile Webstore Customer   

        CUSTOMER_TYPE  CUSTOMER_CATEGORY_DESC  
113758       Eprofile                Hospital  
444247       Eprofile         Ambulatory Care  
444252       Eprofile         Ambulatory Care  
444256       Eprofile         Ambulatory Care  
444257       Eprofile         Ambulatory Care  

[5 rows x 25 columns]

In [116]:
def is_a_match(thing_1, thing_2, threshold):
    if thing_1 == thing_2:
        match = True
    elif thing_1 in thing_2:
        match = True
    elif thing_2 in thing_1:
        match = True
    elif fuzz.ratio(thing_1, thing_2)>threshold:
        match = True
        print('')
        print(fuzz.ratio(thing_1, thing_2))
        print('------------------------------------')
    else:
        match = False
    return(match)

In [28]:
def fix(component):
    component = component.strip().upper()
    return component
def error_handle(parsed_string):
    new_dict = {}
    for thing in parsed_string:
        if thing[1] in new_dict.keys():
            a_list = [new_dict[thing[1]], thing[0]]
            new_dict[thing[1]] = max(a_list, key=len)
        else:
            new_dict[thing[1]] = thing[0]
    return(new_dict)
def clean_address_two(add_1):
    add_1 = add_1.strip()
    if add_1 == 'None':
        addr_1 = ''
    elif add_1 == 'NAN':
        addr_1 = ''
    else:
        addr_1 = ', ' + add_1
    return(addr_1)

def get_address_dict(address):
    try:
        address_dict = usaddress.tag(address)[0]
    except usaddress.RepeatedLabelError as e:
        print(e.original_string)
        address_dict = error_handle(e.parsed_string)
        print('')
    return address_dict
        
def parse_gov_address(moar):
    dict_list = []
    for row in moar.itertuples():
        addr_2 = clean_address_two(row.adr_ln_2)
        address = f'{fix(row.adr_ln_1)}{addr_2}, {fix(row.cty)}, {fix(row.st)}'
        address_dict = get_address_dict(address)
        address_dict['adrs_id'] = row.adrs_id
        address_dict['PHONE'] = row.phn_numbr
        address_dict['ZIPCODE'] = row.zip
        address_dict['ZIP'] = use.fix_zipcode(row.zip)
        dict_list.append(address_dict)
    parsed_df = pd.DataFrame(dict_list)
    parsed_df.dropna(how='all', axis=1, inplace=True)
    return (parsed_df)

def parse_cred_address(moar):
    dict_list = []
    for row in moar.itertuples():
        addr_2 = clean_address_two(row.ADDRESS_LINE_2)
        address = f'{fix(row.ADDRESS_LINE_1)}{addr_2}, {fix(row.CITY)}, {fix(row.STATE)}'
        address_dict = get_address_dict(address)
        address_dict['ORG_ID'] = row.ORG_ID
        address_dict['ZIPCODE'] = row.ZIPCODE
        address_dict['ZIP'] = use.fix_zipcode(row.ZIPCODE)
        dict_list.append(address_dict)
    parsed_df = pd.DataFrame(dict_list)
    parsed_df.dropna(how='all', axis=1, inplace=True)
    return (parsed_df)

In [25]:
gov_adds = gov.drop_duplicates('adrs_id')

In [29]:
gov_parsed = parse_gov_address(gov_adds)

1260 SILAS DEANE HWY 110, WETHERSFIELD, CT

7625 WISCONSIN AVE, 250 APEX MEDICAL SERVICES, BETHESDA, MD

SUITE 408 TORRE SAN FRANCISCO, 369 DE DIEGO AVE, RIO PIEDRAS, PR

CARR 185 KM 15, INSTITUTO DE MEDICINA DE FAMILIA DE CEDROS, CAROLINA, PR

1110 EASTERN PKWY, PIERRE TOUSSAINT FAM HLTH CTR, BROOKLYN, NY

CARR 2 KM, 4 HOSPITAL DE LA CONCEPCION, SAN GERMAN, PR

1475 WILSON AVE, WILSON MED BLDG OFIC 3B, SAN JUAN, PR

ROAD 21 URB LAS LOMAS, TORRE DEL METROPOLITANO 178 OFI 205 HOSPITAL METRO, SAN JUAN, PR

1 GUSTAVE LEVY PLACE, NEW YORK, NY

5501 OLD YORK RD WCB 4TH FLR, EINSTEIN CT SURGERY ASSOC, PHILADELPHIA, PA

CARR 2 KM, 1 BO CANDELARIA, ARECIBO, PR

BAYAMON MEDICAL PLAZA, SUITE 711 1845 CARR. 2 KM 11.7, BAYAMON, PR

51 MENDEZ VIGO ST, CORNER OF PERAL ST, MAYAGUEZ, PR

CARR 111 KM 2, BO PALMAR, AGUADILLA, PR

1056 MUNOZ RIVERA AVE, FIRST FEDERAL SUITE 403, SAN JUAN, PR

CARR 2 KM, 1 MARGINAL 270, HATILLO, PR

1 SEARS DR, SUITE 403 4TH FLOOR, PARAMUS, NJ

ST 2 KM, 57 SUITE 105, MAYAG

CARR 129 KM 1, HOSPITAL PAVIA ARECIBO, ARECIBO, PR

AVE PONCE DE LEON 715 PDA, 2 CLINICAS EXTERNAS HOSP AUXILIO MUTUO, SAN JUAN, PR

CARR 685 KM, 9 BO TIERRAS NUEVAS, MANATI, PR

CARR 478 KM, 4 BARRIO SAN ANTONIO, QUEBRADILLAS, PR

775 E ROUTE 70 F180, OPHTHALMIC PARTNERS OF PA NJ, MARLTON, NJ

100 W LANCASTER AVE, SUITE 441 LANK OFC W, WYNNEWOOD, PA

3015 N BALLAS RD, PHYSICIAN SERVICES, ST LOUIS, MO

555 N NEW BALLAS RD, 265 SUBURBAN SURGICAL, ST LOUIS, MO

655 N CENTRAL AVE, 1776 ACT MEDICAL GROUP INC, GLENDALE, CA

2225 PONCE BY PASS, EDIFICIO PARRA SUITE 606, PONCE, PR

840 S WOOD ST MC, 787 UIC MEDICINE, CHICAGO, IL

6926 NE 4TH PLAIN BLVD, VANCOUVER, WA

URB ATENAS CARR 2 INTER, 668 MANATI MEDICAL CENTER SUITE 201, MANATI, PR

24 W WASHINGTON ST, BRADFORD MED GRP OF UPMC HAMET, BRADFORD, PA

CARR 129 KM 8 SAN LUIS, HOSPITAL PAVIA SUITE 104, ARECIBO, PR

1115 S SUNSET AVE, QUEEN OF VLY HOSP, WEST COVINA, CA

341 S MARINE CORPS DR RK PLZ, 104 GUAM ENT LLC, TAMUNING, GU

4401 WORNA

3006 N COUNTY RD, 25A SUITE 102, TROY, OH

CARR 119 KM, 0 BO PIEDRAS BLANCAS, SAN SEBASTIAN, PR

800 MANOR RD, 4 SUITE 4, STATEN ISLAND, NY

6140 SW 70 ST, 200 LARKIN MULTISPECIALTY CLINIC, SOUTH MIAMI, FL

7520 MONTGOMERY BLVD NE E, 4 JOHN A CAMPA III MD PC, ALBUQUERQUE, NM

ROAD 2 KM, 7 HERMANOS MELENDEZ HOSPITAL, BAYAMON, PR

PR CHILDRENS HOSPITAL, ROAD 2 KM 11.7 SUITE 910, BAYAMON, PR

CARR 455 INT 454 KM, SUITE 3, CAMUY, PR

1098 W BALTIMORE PK, OP PAVILION SUIE 3311, MEDIA, PA

600 BLVD MONTANA, 329 ARBOLES DE MONTEHIEDRA, SAN JUAN, PR

CARR 2 KM, SUITE 1, ARECIBO, PR

CARR 199 EDIF 198, 1 ROYAL TOWN, BAYAMON, PR

SAN GERMAN MED PLAZA, CARR 2 KM 174 SUITE 211, SAN GERMAN, PR

600 7TH ST SE, 101 OUTPATIENT PALLIATIVE CARE CLINIC, CEDAR RAPIDS, IA

788 8TH ST SE, 400 MERCY CARDIOLOGY CLINIC, CEDAR RAPIDS, IA

CARR 844 KM, 2 CUPEY BAJO, SAN JUAN, PR

1098 W BALTIMORE PIKE, OUTPATIENT PAVILION SUITE 3405, MEDIA, PA

ROAD 2 KM, 1 COND ARECIBO MEDICAL CENTER SUITE 202, ARECIBO, PR

CAL

112 N 7TH STREET 3RD FLOOR CHAMBERSBURG HOSP, WELLSPAN BEHAVIORAL HEALTH, CHAMBERSBURG, PA

3935 I 49 S SERVICE RD, OPELOUSAS, LA

840 E 29TH ST, FREMONT HLTH SURG CTR, FREMONT, NE

350 ENGLE ST, BERRIE BLDG SUITE 6501, ENGLEWOOD, NJ

8282 EL RIO ST, 140 UWH OF TEXAS PLLC, HOUSTON, TX

660 S 200 E, 250 SACRED CIRCLE HEALTHCARE, SALT LAKE CITY, UT

12955 SW 132ND ST, BUILDING 3B SUITE 104, MIAMI, FL

2001 WATERDAM PLAZA DR, 108 MON VALE BREAST CARE, MCMURRAY, PA

490 A W ZIA RD, 260 CHRISTUS ST. VINCENT DERMATOLOGY SP, SANTA FE, NM

2321 IRA E WOODS, 180 DERMATOLOGY ASSOCIATES, GRAPEVINE, TX

2811 E 15TH ST, 102 SEVA MED CARE, TULSA, OK

4432 E BRISTOL RD SHOPPING CTR UNIT, 1B ARS TREATMENT CENTER PC, FEASTERVILLE TREVOSE, PA

395 WESTFIELD RD, HEMATOLOGY ONCOLOGY OF INDIANA PC, NOBLESVILLE, IN

4100 WATERMAN WAY, FLORIDA CANCER SPECIALISTS PL, TAVARES, FL

801 N MUR LEN RD, 201 OHFM MURLEN, OLATHE, KS

1616 W AVE, K8 APT C206, LANCASTER, CA

163 -03 HORACE HARDING EXPRESSWAY, LOWER LEV

50 N MEDICAL DR, UNIVERSITY OF UTAH HOSPITAL PMANDR, SALT LAKE CITY, UT

4260 PLYMOUTH RD, U OF M SLEEP MEDICINE, ANN ARBOR, MI

67 ROUTE 37 W, RIVERWOOD 2 ROOM 103, TOMS RIVER, NJ

67 HWY 37 W, RIVERWOOD 1 1ST FLOOR, TOMS RIVER, NJ

4100 SW I ST, 200 MERCY CLINIC PRIMARY CARE I STREET, BENTONVILLE, AR

633 E S BLVD, 1200 ALAN KLEIN MD, ROCHESTER HILLS, MI

1310 WISCONSIN ST, 103 MHPP NORTH OTTAWA FAMILY MEDICINE, GRAND HAVEN, MI

11320 S M 43 HWY 2, BORGESS MED. COMMONS DELTON, DELTON, MI

200 N PARK ST, WEST MICHIGAN CANCER CENTER, KALAMAZOO, MI

5050 NE HOYT ST, 315 PROV NEUROL SPEC EAS, PORTLAND, OR

5050 NE HOYT ST, 615 PROV NEURO SPEC PLAZ, PORTLAND, OR

16180 SE SUNNYSIDE RD, 102 PROV MED GR HAP VALL, HAPPY VALLEY, OR

5050 NE HOYT ST, 155 PROV MED GRP ARTH CE, PORTLAND, OR

9205 SW BARNES RD, 3RD FLOOR MAT MT3401, PORTLAND, OR

315 SE STONEMILL DR, 220 PROV ST VINCENT HEART CLINICS CARDIO MILL PLAIN, VANCOUVER, WA

4805 NE GLISAN, 6N50 PROV BREAST CR CL EA, PORTLAND, OR

9155 S

...

305 W 15TH ST, 102 UROLOGY CARE CENTER, LIBERAL, KS

305 W 15TH ST, 101 ORTHOPEDIC AND SPORTS MED CARE CTR, LIBERAL, KS

420 W LINFIELD TRAPPE RD, ENDOSCOPY ASSOCIATES OF VALLEY FORG, LIMERICK, PA

420 W LINFIELD TRAPPE RD, OUTPATIENT AND SURGERY CENTER AT LIMERICK, LIMERICK, PA

60 E END AVE, PRIVATE ENTRANCE, NEW YORK, NY

5317 E 16TH ST, JANE PAULEY CHC AT 16TH STREET INC, INDIANAPOLIS, IN

500 W BROADWAY, BROADWAY BLDG 4TH FLOOR, MISSOULA, MT

15435 W 134TH PL, 103 OHFM BLACKFOOT, OLATHE, KS

20375 W 151ST ST, 151 OHFM OLATHE MEDICAL PARK, OLATHE, KS

411 10TH ST SE, 150 UNIVERSITY OF IA FAM CHILD HOSP PEDS CEDAR RAPIDS, CEDAR RAPIDS, IA

411 10TH ST SE, 1200 CEDAR RAPIDS DERM OF UNIV OF IA HEALTH CARE, CEDAR RAPIDS, IA

PRESBYTERIAN VILLAGE N, 8600 SKYLINE DR, DALLAS, TX

1864 HILLCREST RD, HILLCREST OF NORTH DALLAS, DALLAS, TX

7724 S 5600, SUITE 102 WEST JORDAN, WEST JORDAN, UT

1272 W MAIN ST, DOCTORS PARK BLDG 5, NEWARK, OH

1901 S UNION AVE, A244 MC PAIN MNGMT CLINIC, TACOMA,

100 E COLLEGE DR, VASCULAR INSTITUTE OF THE ROCKIES, COLBY, KS

10720 NALL AVE, UNIVERSITY OF KANSAS INDIAN CREEK CAMPUS, OVERLAND PARK, KS

1000 E 101ST TERRACE, UNIV KS CNCR CNTR S, KANSAS CITY, MO

2240 N BANK DR, UPPER ARL SURG CTR, COLUMBUS, OH

1715 N GEORGE MASON DR, 101 THE RETINA CENTERS OF WASHINGTON, ARLINGTON, VA

CARR 857 KM, 4 BO CANOVANILLAS, CAROLINA, PR

1700 N OREGON ST, 710 EL PASO ORTHO WEST, EL PASO, TX

2225 PONCE BY PASS, EDIFICIO PARRA SUITE 101, PONCE, PR

1111 N MOUNT AUBURN RD, WOMEN FIRST OF SOUTHEAST HEALTH, CAPE GIRARDEAU, MO

901 ROUTE 168 301-305, TURNERSVILLE, NJ

105 KINGS WAY W, HURFFVILLE CROSS KEYS ROAD, SEWELL, NJ

1000 LINCOLN DR E, 1000 LINCOLN CTR, MARLTON, NJ

86 ST FELIX ST, TBHC ST FELIX 8TH FL, BROOKLYN, NY

250 E BASSE RD, 205 NORTHEAST OB/GYN ASSOCIATES, SAN ANTONIO, TX

1139 E SONTERRA BLVD, 205 NORTHEAST OB/GYN ASSOCIATES, SAN ANTONIO, TX

178 HWY 105 EXT 101, BOONE, NC

2503 FOREST HILLS W RD B, WILSON, NC

159 N 3RD ST E, CANCER SPECIA

1265 WAYNE AVE, 301 119 PROFESSIONAL CTR, INDIANA, PA

6200 SW 73RD ST, S. MIAMI HOSPITAL, SOUTH MIAMI, FL

5701 N PORTLAND AVE, 105 EDWARD D JONES MD, OKLAHOMA CITY, OK

97 W PHILLIP RD, VICTORY CENTRE OF VERNON HILLS, VERNON HILLS, IL

180 W HALF DAY RD, SUNRISE OF BUFFALO GROVE, BUFFALO GROVE, IL

1901 S UNION AVE B, Suite 5003, TACOMA, WA

2900 N, 35 MOB 1 SUITE 409, DENTON, TX

CARR 2 KM, 1 AVE SEVERIANO CUEVAS BO CAIMITAL BAJO, AGUADILLA, PR

227 N LOOP 1604 E, 150 TWO TWIN OAKS, SAN ANTONIO, TX

3535 S JEFFERSON AVE, 304 JAY MAHADEVAN MD, ST LOUIS, MO

3441 24TH AVE NW, 105 R BRUCE PARKER MD, NORMAN, OK

12596 W BAYAUD AVE, 205 MILE HIGH REGENERATIVE AND PAIN, LAKEWOOD, CO

8 0 CARR 152 KM, BARRANQUITAS, PR

2141 S ALTERNATE, A1A SUITE 430, JUPITER, FL

4373 UNION ST, SUITE CA, FLUSHING, NY

9570 SW 107 AVENUE C, Suite 204, MIAMI, FL

SUITE BO BRENAS, Suite 171, VEGA ALTA, PR

720 ESKENAZI AVE OCC 2ND FLR, INDIANAPOLIS, IN

901 E SUNFLOWER RD, BOLIVAR MEDICAL CTR, CLEVELAND, MS


1710 E SAUNDERS ST B, Suite 350, LAREDO, TX

1316 BLACK RIVER N BLVD, ROME, NY

314 E MAIN ST, 302 KELWAY PLAZA, NEWARK, DE

AVE SEVERIANO CUEVAS, 18 CARR 460 CAIMITAL BAJO, AGUADILLA, PR

4541 N JOSEY LANE, 230 EXCALIBUR PAIN AND REHAB, CARROLLTON, TX

13119 NEW HALLS FERRY RD, DAVITA HALLS FERRY RD, FLORISSANT, MO

450 N LINDBERGH BLVD, DAVITA ST LOUIS WEST, SAINT LOUIS, MO

1942 W COUNTY RD 419, 1060 FRONTLINE PRIMARY CARE, CHULUOTA, FL

40005 10TH W ST, 213 OLYMPIC ORTHOPEDIC AND SPORTS, PALMDALE, CA

2 STATE ROUTE 27 100A, EDISON, NJ

SAN JOSE PLAZA OFI, 8 CARR 308 KM 0.3, MAYAGUEZ, PR

800 BIESTERFIELD RD, 4009 BROCK BUILDING, ELK GROVE VILLAGE, IL

1845 CARR, 2 SUITE 607, BAYAMON, PR

33 S DELAWARE AVE, 104 B RIVERVIEW PLAZA, YARDLEY, PA

1305 WONDER WORLD DR, 101 CTMC, SAN MARCOS, TX

13885 US, 1 SUITE 6, SEBASTIAN, FL

AVE DEGETAU, 2A CALLE 1 EXT EL VERDE, CAGUAS, PR

200 JOHN W HOOVER PKWY, BURNET, TX

CARR 1 KM, 8 BO BEATRIZ, CIDRA, PR

16215 SR, 50 SUITE 102, CLERMONT, FL



6919N DALE MABRY HWY 320, TAMPA, FL

365 COUNTY RD, 39A SUITE 15 16 BENTON PLZ, SOUTHAMPTON, NY

44121 HARRY BYRD HWY 250, ASHBURN, VA

2596 INTERSTATE 55 SERVICE RD, TRI STATE ADV SURGERY CTR, MARION, AR

1328 SOUTHERN AVE SE, 205 DC, WASHINGTON, DC

CARR 829 KM, 8 BARRIO PINAS, TOA ALTA, PR

3975 I 49 S SERVICE RD, SUITE 105, OPELOUSAS, LA

610 PROVIDENCE PARK E DR, Suite 104, MOBILE, AL

2975 NORHTWEST 99 AVE, HARBOR CHASE OF CORAL SPRINGS, CORAL SPRINGS, FL

5656 EDWARDS RANCH RD, 202 MATTHEW H STEELE MD COSMETIC AND RECONSTRUCTIVE PL, FORT WORTH, TX

555 E TACHEVAH DR, BLDG 1 WEST SUITE 202, PALM SPRINGS, CA

221 W COLORADO BLVD, PAVILION II SUITE 829, DALLAS, TX



In [36]:
cred_adds = good_cred.drop_duplicates('ORG_ID')

In [37]:
cred_parsed = parse_cred_address(cred_adds)

4700 WISSAHICKON AVE STE 110 STE 118, PHILADELPHIA, PA

169 RIVERSIDE DR, 169 Riverside Dr, BINGHAMTON, NY

THREE GATEWAY CENTER, 20TH FLOOR, 401 Liberty Ave Ste 2000, PITTSBURGH, PA

133 OLD ROAD TO 9 ACRE COR, CONCORD, MA

7625 HOSPITAL DR, 7625 Hospital Dr, DUBLIN, OH

826 W KING ST, 826 W King St, OWOSSO, MI

PO BOX 4769, PO Box 4769, JOPLIN, MO

1700  LINDBERG  DR, 1700 Lindberg Dr, SLIDELL, LA

MASTIN BLDG - 6TH FLOOR, 2451 University Hospital Dr, MOBILE, AL

503 W CAROLINA AVENUE, 503 W Carolina Ave, VARNVILLE, SC

1 GRAND AVE, 1 Grand Ave, SN LUIS OBISP, CA

4TH FLOOR, ROOM 453, 11401 Bloomfield Ave, NORWALK, CA

6TH FLOOR SOUTH, 2830 Calder St, BEAUMONT, TX

1555 BARRINGTON RD, DOCTORS BUILDING 3,, Suite 0400, HOFFMAN ESTATES, IL

3920 S SHIELDS ST, 3920 S Shields St, FORT COLLINS, CO

3201 N FEDERAL HIGHWAY, SUITE 212, Suite 102, FORT LAUDERDALE, FL

2620 ELM HILL PIKE, 2620 Elm Hill Pike, NASHVILLE, TN

20555 VICTOR PKWY, Mail Stop W3 B, LIVONIA, MI

ST. 229, 110 West Rd Ste

In [42]:
good_cred_parsed = pd.merge(good_cred, cred_parsed, on='ORG_ID')

In [45]:
gov_all_parsed = pd.merge(gov, gov_parsed, on='adrs_id')

In [46]:
just_a_test = pd.merge(good_cred_parsed, gov_all_parsed, on='ME', suffixes = ['_CRED','_GOV'])

In [ ]:
for col in just_a_test.columns:
    print(col)

In [54]:
just_a_test = just_a_test.fillna('None')

In [129]:
dicts =[]
for row in just_a_test.itertuples():
    if row.STATE == row.st:
        if row.AddressNumber_GOV == row.AddressNumber_CRED and is_a_match(row.StreetName_GOV, row.StreetName_CRED,85):
            print(f'{row.adr_ln_1} is {row.ADDRESS_LINE_1}')
            new_dict = {
                'ME': row.ME,
                'adrs_id': row.adrs_id,
                'ORG_ID': row.ORG_ID,
                'CATEGORY': row.CUSTOMER_CATEGORY_DESC,
                'DATE': row.FULL_DT,
                'STATE': row.STATE,
                'GOV_ADDR': row.adr_ln_1,
                'CRED_ADDR': row.ADDRESS_LINE_1,
                'GOV_ZIP': row.ZIP_GOV,
                'CRED_ZIP':row.ZIP_CRED
                }
            dicts.append(new_dict)

910 WALLACE AVE is 910 Wallace Ave
1141 HOSPITAL DR NW is 1141 Hospital Dr NW
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
911 BYPASS RD is 911 Bypass Rd
911 BYPASS RD is 911 Bypass Rd
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 9

736 N BATTLEFIELD BLVD is 736 Battlefield Blvd N
736 N BATTLEFIELD BLVD is 736 Battlefield Blvd N
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200

91
------------------------------------
202 DUKE OF GLOUCESTER SWST is 202 Duke Gloucester St SW
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
2215 LANDOVER PL is 2215 Landover Pl
2215 LANDOVER PL is 2215 Landover Pl
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania Ave Ste 200
10401 SPOTSYLVANIA AVE is 10401 Spotsylvania A


88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

88
-----------------

1501 RIVER POINTE DR is 1501 River Pointe Dr Ste 200
1501 RIVER POINTE DR is 1501 River Pointe Dr Ste 200
1017 S TRAVIS AVE is 1017 S Travis Ave
1017 S TRAVIS AVE is 1017 S Travis Ave
1100 BUTTE ST is 1100 Butte St
9301 N CENTRAL EXPY is 9301 N Central Expy Ste 100
9301 N CENTRAL EXPY is 9301 N Central Expy Ste 100
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
7737 SOUTHWEST FWY is 7737 Southwest Fwy Ste C-98
690 S LOOP 336 is 690 S Loop 336 W Ste 130
510 W TIDWELL RD is 510 W Tidwell Rd
510

1500 S MAIN ST is 1500 S Main St
5501 S MCCOLL RD is 5501 S McColl Rd
2000 S MAYS ST is 2000 S Mays St Ste 201
2000 S MAYS ST is 2000 S Mays St Ste 201
1300 MURCHISON DR is 1300 Murchison Dr Ste 200
1451 EL CAMINO REAL is 1451 El Camino Real
1451 EL CAMINO REAL is 1451 El Camino Real
1451 EL CAMINO REAL is 1451 El Camino Real
10000 W COLONIAL DR is 10000 W Colonial Dr Ofc
221 W COLORADO BLVD is 221 W Colorado Blvd Ste 625
221 W COLORADO BLVD is 221 W Colorado Blvd Ste 625
9301 N CENTRAL EXPY is 9301 N Central Expy Ste 100
9301 N CENTRAL EXPY is 9301 N Central Expy Ste 100
9301 N CENTRAL EXPRESSWAY is 9301 N Central Expy Ste 100
9301 N CENTRAL EXPRESSWAY is 9301 N Central Expy Ste 100
1705 JACKSON ST is 1705 Jackson St
1705 JACKSON ST is 1705 Jackson St
2001 MEDICAL PKWY is 2001 Medical Pkwy
425 POST RD is 425 Post Rd
425 POST RD is 425 Post Rd
4641 ROOSEVELT BLVD is 4641 Roosevelt Blvd
4641 ROOSEVELT BLVD is 4641 Roosevelt Blvd
211 N EDDY ST is 211 N Eddy St
211 N EDDY ST is 211 N Eddy

...

300 RIVERSIDE DR E is 300 Riverside Dr E Ste 4300
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St
55 W TIETAN ST is 55 W Tietan St

88
------------------------------------
1600 MEDICAL CTR DR is 1600 Medical Center Dr
900 HOSPITAL DR is 900 Hospital Dr
900 HOSPITAL DR is 900 Hospital Dr
900 HOSPITAL DR is 900 Hospital Dr
900 HOSPITAL DR is 900 Hospital Dr
10101 FOREST HILL BLVD is 10101 Forest Hill Blvd
10101 FOREST HILL BLVD is 10101 Forest Hill Blvd
539 E PRUDHOMME ST is 539 E Prudhomme St
539 E PRUDHOMME ST is 539 E Prudhomme St
29 E 29TH ST is 29 E 29th St
29 E 29TH ST is 29 E 29th St
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1331 E WYOMING A

13950 BRANDYWINE RD is 13950 Brandywine Rd Lowr Level
13950 BRANDYWINE RD is 13950 Brandywine Rd Lowr Level
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
1111 W LA PALMA AVE is 1111 W La Palma Ave
101 COLE AVE is 101 Cole Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PROSPECT AVE is 30 Prospect Ave
30 PR

615 OLD SYMSONIA RD is 615 Old Symsonia Rd
615 OLD SYMSONIA RD is 615 Old Symsonia Rd

90
------------------------------------
80 HUMPHREYS CTR DR is 80 Humphreys Center Dr Ste 101

90
------------------------------------
80 HUMPHREYS CTR DR is 80 Humphreys Center Dr Ste 101
955 RIBAUT RD is 955 Ribaut Rd
955 RIBAUT RD is 955 Ribaut Rd
130 E LOCKLING AVE is 130 E Lockling St
130 E LOCKLING AVE is 130 E Lockling St
130 E LOCKLING AVE is 130 E Lockling St
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE is 609 E Orangeburg Ave Bldg B
609 E ORANGEBURG AVE i

1200 N W AVE is 1200 N West Ave
1200 N W AVE is 1200 N West Ave
1200 N W AVE is 1200 N West Ave
3203 TOWER OAKS BLVD is 3203 Tower Oaks Blvd
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
137 N LHS DR is 137 N LHS Drive
1630 S BROWNLEE BLVD is 1630 S Brownlee Blvd
1630 S BROWNLEE BLVD is 1630 S Brownlee Blvd
365 MONTAUK AVE is 365 Montauk Ave
365 MONTAUK AVE is 365 Montauk Ave
365 MONTAUK AVE is 365 Montauk Ave
2740 W FOSTER AVE is 2740 W Foster Ave Ste 310
2740 W FOSTER AVE is 2740 W Foster Ave Ste 310
1900 STATE ST is 1900 Stat

3883 74TH AVE NE is 3883 74th Ave NE
3883 74TH AVE NE is 3883 74th Ave NE
23900 ORCHARD LAKE RD is 23900 Orchard Lake Rd Ste 50
605 N WESTOVER BLVD is 605 N Westover Blvd
5002 W LEMON ST is 5002 W Lemon St
5002 W LEMON ST is 5002 W Lemon St
URB ATENAS 200 CALLE HERNANDEZ CARRION is Susoni #116
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
1849 SAVAGE RD is 1849 Savage Rd
112 GAINSBOROUGH SQ is 112 Gainsborough Sq Ste 200
16260 VENTURA BLVD is 16260 Ventura Blvd Ste 309
16260 VENTURA BLVD is 16260 Ventura Blvd Ste 309
9500 MENTOR AVE is 9500 Mentor Ave Ste 380
9500 MENTOR AVE is 9500 Mentor Ave Ste 380
9500 MEN

In [134]:
purity = pd.DataFrame(dicts)

In [223]:
other_dicts =[]
for row in just_a_test.itertuples():
    if row.STATE == row.st:
        if is_a_match(fix(row.adr_ln_1), fix(row.ADDRESS_LINE_1), 90):
            print(f'{row.adr_ln_1} is {row.ADDRESS_LINE_1}')
            new_dict = {
                'ME': row.ME,
                'adrs_id': row.adrs_id,
                'ORG_ID': row.ORG_ID,
                'CATEGORY': row.CUSTOMER_CATEGORY_DESC,
                'DATE': row.FULL_DT,
                'STATE': row.STATE,
                'GOV_ADDR': row.adr_ln_1,
                'CRED_ADDR': row.ADDRESS_LINE_1,
                'GOV_ZIP': row.ZIP_GOV,
                'CRED_ZIP': row.ZIP_CRED
                }
            other_dicts.append(new_dict)

910 WALLACE AVE is 910 Wallace Ave
1141 HOSPITAL DR NW is 1141 Hospital Dr NW
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
910 WALLACE AVE is 910 Wallace Ave
911 BYPASS RD is 911 Bypass Rd
911 BYPASS RD is 911 Bypass Rd

93
------------------------------------
908 WALLACE AVE is 910 Wallace Ave

93
------------------------------------
908 WALLACE AVE is 910 Wallace Ave

93
------------------------------------
908 WALLACE AVE is 910 Wallace Ave

9

8080 BLUEBONNET BLVD is 8080 Bluebonnet Blvd
1541 KINGS HWY is 1541 Kings Hwy
1541 KINGS HWY is 1541 Kings Hwy
1541 KINGS HWY is 1541 Kings Hwy
1500 LINE AVE is 1500 Line Ave Ste 206
8080 BLUEBONNET BLVD is 8080 Bluebonnet Blvd
10101 PARK ROWE AVE is 10101 Park Rowe Ave
10101 PARK ROWE AVE is 10101 Park Rowe Ave
4900 MEDICAL DR is 4900 Medical Dr
8080 BLUEBONNET BLVD is 8080 Bluebonnet Blvd
1541 KINGS HWY is 1541 Kings Hwy
1541 KINGS HWY is 1541 Kings Hwy
1541 KINGS HWY is 1541 Kings Hwy
1541 KINGS HWY is 1541 Kings Hwy
165 BEECH SPRINGS RD is 165 Beech Springs Rd
165 BEECH SPRINGS RD is 165 Beech Springs Rd
415 S 28TH AVE is 415 S 28th Ave
415 S 28TH AVE is 415 S 28th Ave
1500 LINE AVE is 1500 Line Ave Ste 206
1500 LINE AVE is 1500 Line Ave Ste 206
107 FRONT ST is 107 Front St Ste 1107
8080 BLUEBONNET BLVD is 8080 Bluebonnet Blvd
8080 BLUEBONNET BLVD is 8080 Bluebonnet Blvd
4324 VETERANS MEMORIAL BLVD is 4324 Veterans Memorial Blvd Ste 101
4324 VETERANS MEMORIAL BLVD is 4324 Veterans 

602 N ACADIA RD is 602 N Acadia Rd
602 N ACADIA RD is 602 N Acadia Rd

93
------------------------------------
604 N ACADIA RD is 602 N Acadia Rd

93
------------------------------------
604 N ACADIA RD is 602 N Acadia Rd

93
------------------------------------
604 N ACADIA RD is 602 N Acadia Rd

93
------------------------------------
604 N ACADIA RD is 602 N Acadia Rd

95
------------------------------------
1103 KALISTE SALOOM RD is 1101 Kaliste Saloom Rd

95
------------------------------------
1103 KALISTE SALOOM RD is 1101 Kaliste Saloom Rd
501 KEYSER AVE is 501 Keyser Ave
336 22ND AVE N is 336 22nd Ave N
336 22ND AVE N is 336 22nd Ave N
9118 BLUEBONNET CENTRE BLVD is 9118 Bluebonnet Centre Blvd
9118 BLUEBONNET CENTRE BLVD is 9118 Bluebonnet Centre Blvd
9118 BLUEBONNET CENTRE BLVD is 9118 Bluebonnet Centre Blvd
9118 BLUEBONNET CENTRE BLVD is 9118 Bluebonnet Centre Blvd
118 N HOSPITAL DR is 118 N Hospital Dr
118 N HOSPITAL DR is 118 N Hospital Dr
602 N ACADIA RD is 602 N Acadia R

1901 TATE SPRINGS RD is 1901 Tate Springs Rd
1901 TATE SPRINGS RD is 1901 Tate Springs Rd
8700 STONY POINT PKWY is 8700 Stony Point Pkwy Ste 100
8700 STONY POINT PKWY is 8700 Stony Point Pkwy Ste 100
1102 S JEFFERSON ST is 1102 S Jefferson St
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
2201 LEXINGTON AVE is 2201 Lexington Ave
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200

94
------------------------------------
2405 ATHERHOLT RD is 2401 Atherholt Rd
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
241 CORPORATE BLVD is 241 Corporate Blvd Ste 200
8700 STONY POINT PKWY is 8700 Stony Point Pkwy Ste 100
8700 STONY POINT PKWY is 8700 Stony Point Pkwy Ste 100
2900 1ST AVE is 2900 1st Ave
744 S WEBSTER AVE is 744 S Webster Ave
744 S WEBSTER AVE is 744 S Webster Ave
744 S WEBSTER AVE is 744 S Webster Ave
744 S WEBSTER AVE is 744 S Webster Av


93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd
5501 S MCCOLL RD is 5501 S McColl Rd
5501 S MCCOLL RD is 5501 S McColl Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
------------------------------------
27700 MEDICAL CTR RD is 27700 Medical Center Rd

93
--------------------------------

...

610 SPARTA RD is 610 Sparta Rd
610 SPARTA RD is 610 Sparta Rd
610 SPARTA RD is 610 Sparta Rd
800 W 5TH AVE is 800 W 5th Ave
800 W 5TH AVE is 800 W 5th Ave
800 W 5TH AVE is 800 W 5th Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

91
------------------------------------
2401 W BELEVEDERE AVE is 2401 West Belvedere Ave

93
------------------------------------
2401 W BELVEDERE AVE is 2401 West Belvedere Ave

93
-

1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1 ROBERT WOOD JOHNSON PL is 1 Robert Wood Johnson Pl
1321 COLBY AVE is 1321 Colby Avenue
1321 COLBY AVE is 1321 Colby Avenue

94
------------------------------------
36000 EUCLID AVE is 36100 Euclid Ave
602 INDIANA AVE is 602 Indiana Ave
602 INDIANA AVE is 602 Indiana Ave
602 INDIANA AVE is 602 Indiana Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S National Ave
901 S NATIONAL AVE is 901 S Nation

40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
40 OLD RIDGEBURY RD is 40 Old Ridgebury Rd Ste 201
2550 S DOUGLAS RD is 2550 S Douglas Rd
2550 S DOUGLAS RD is 2550 S Douglas Rd
2550 S DOUGLAS RD is 2550 S Douglas Rd
2550 S DOUGLAS RD is 2550 S Douglas Rd
2550 S DOUGLAS RD is 2550 S Douglas Rd
2550 S DOUGLAS RD is 2550 S Douglas Rd
9961 SIERRA AVE is 9961 Sierra Ave
9961 SIERRA AVE is 9961 Sierra Ave
9961 SIERRA AVE is 9961 Sierra Ave
9961 SIERRA AVE is 9961 Sierra Ave
7700 OLD BRANCH AVE is 7700 Old Branch Ave Ste A101
7700 OLD BRANCH AVE is 7700 Old Branch Ave Ste A101
21275 OLEAN BLVD is 21275 Olean Blvd
21275 OLEAN BLVD is 21275 Olean Blvd
21275 OLEAN BLVD is 21275 Olean Blvd
21275 OLEAN BLVD is 21275 Olean Blvd
21275 OLEAN BLVD 

1703 S MERIDIAN is 1703 S Meridian Ste 201
1703 S MERIDIAN is 1703 S Meridian Ste 201
1703 S MERIDIAN is 1703 S Meridian Ste 201
1703 S MERIDIAN is 1703 S Meridian Ste 201
1703 S MERIDIAN is 1703 S Meridian Ste 201
1703 S MERIDIAN is 1703 S Meridian Ste 201
555 MARIN ST is 555 Marin St Ste 270 # A
1401 S RANGERVILLE RD is 1401 S Rangerville Rd
1401 S RANGERVILLE RD is 1401 S Rangerville Rd
1401 S RANGERVILLE RD is 1401 S Rangerville Rd
1401 S RANGERVILLE RD is 1401 S Rangerville Rd
27101 SCHOENHERR RD is 27101 Schoenherr Rd Ste 300
27101 SCHOENHERR RD is 27101 Schoenherr Rd Ste 300
541 SUNSET LN is 541 Sunset Ln Ste 100
541 SUNSET LN is 541 Sunset Ln Ste 100
259 MONROE AVE is 259 Monroe Ave
259 MONROE AVE is 259 Monroe Ave
1 SASCO HILL RD is 1 Sasco Hill Rd Ste 3
1 SASCO HILL RD is 1 Sasco Hill Rd Ste 3
1 SASCO HILL RD is 1 Sasco Hill Rd Ste 3
1 SASCO HILL RD is 1 Sasco Hill Rd Ste 3
14003 LAKESHORE BLVD is 14003 Lakeshore Blvd
14003 LAKESHORE BLVD is 14003 Lakeshore Blvd
14003 LAKESHO

10058 S MOUNTAIN RD is 10058 S Mountain Rd
10058 S MOUNTAIN RD is 10058 S Mountain Rd
1150 RESERVOIR AVE is 1150 Reservoir Ave Ste 100
1150 RESERVOIR AVE is 1150 Reservoir Ave Ste 100
1150 RESERVOIR AVE is 1150 Reservoir Ave Ste 100
1150 RESERVOIR AVE is 1150 Reservoir Ave Ste 100
1201 MEDICAL PARK DR is 1201 Medical Park Dr Ste 101
2400 MOORPARK AVE is 2400 Moorpark Ave Ste 300
2400 MOORPARK AVE is 2400 Moorpark Ave Ste 300
7227 HAMILTON AVE is 7227 Hamilton Ave
301 W MYRTLE ST is 301 W Myrtle St
301 W MYRTLE ST is 301 W Myrtle St
2500 MARTIN LUTHER KING JR BLVD is 2500 Martin Luther King Jr Blvd
2500 MARTIN LUTHER KING JR BLVD is 2500 Martin Luther King Jr Blvd
1958 OCEAN AVE is 1958 Ocean Ave
3101 GARRETT DR is 3101 Garrett Dr


In [224]:
testy = pd.DataFrame(other_dicts)

In [225]:
missing = testy[testy.ME.isin(purity.ME)==False]

In [132]:
len(purity)

19547

In [108]:
purity[purity.ME.isin(testy.ME)==False]

ME                    adrs_id  ORG_ID         CATEGORY  \
128    02105971608  LA700942648AV3932XWXXX400   15280   Health Related   
325    02701730171  MS389302720GR2005XWXXX400    8213  Ambulatory Care   
350    02106952429  LA705864618VI800XXSTXX400    2454         Hospital   
413    49576000102  VA240141372RO202XXSWST500   23842  Ambulatory Care   
426    03607000467  VA233201707CH736XXBLVD400   15352     Managed Care   
...            ...                        ...     ...              ...   
43616  75901850097  IL604501463MO1051X6XXX400    5700  Ambulatory Care   
43619  75901850038  IL604501463MO1051X6XXX400    5700  Ambulatory Care   
43654  04812881987  GA300607902MA335XXNWST300    5638  Ambulatory Care   
43661  03006130380  MS397358917AC8613X12XX400   15798         Hospital   
43683  64914050403  PR006744652MAURBXXCARR601   16555   Health Related   

            DATE STATE                                GOV_ADDR  \
128   2020-05-06    LA                           3932 HWY 90 W   
325   2020-06-11    MS                           2005 HWY 82 W   
350   2019-11-18    LA                           800 E MAIN ST   
413   2020-11-10    VA             202 DUKE OF GLOUCESTER SWST   
426   2020-09-03    VA                  736 N BATTLEFIELD BLVD   
...          ...   ...                                     ...   
43616 2021-04-19    IL                          1051 W ROUTE 6   
43619 2021-04-19    IL                          1051 W ROUTE 6   
43654 2021-04-28    GA                       335 ROSELANE NWST   
43661 2021-04-30    MS                          8613 MS HWY 12   
43683 2021-05-14    PR  URB ATENAS 200 CALLE HERNANDEZ CARRION   

                       CRED_ADDR  
128           3932 US Highway 90  
325            2005 Highway 82 W  
350         800 East Main Street  
413    202 Duke Gloucester St SW  
426       736 Battlefield Blvd N  
...                          ...  
43616  1051 W US Route 6 Ste 100  
43619  1051 W US Route 6 Ste 100  
43654         335 Roselane St NW  
43661         8613 Ms Highway 12  
43683                Susoni #116  

[1908 rows x 8 columns]

In [226]:
check_12 = pd.concat([missing, purity]).sort_values('DATE').drop_duplicates('ME',keep='last')

In [137]:
pd.concat([testy, purity])

ME                    adrs_id  ORG_ID         CATEGORY  \
0      02002061344  KY427542414LE910XXAVEX300    3588         Hospital   
1      02002061344  IN471122164CO1141XNWXX400    2360         Hospital   
2      01642871133  KY427542414LE910XXAVEX300    3588         Hospital   
3      01642871133  KY427542414LE910XXAVEX300    3588         Hospital   
4      01642871133  KY427542414LE910XXAVEX300    3588         Hospital   
...            ...                        ...     ...              ...   
43682  03701870041  ID837027656BO301XXSTXX400    9292  Ambulatory Care   
43683  02101810456  FL324054412PA2500XBLVD600    8130  Ambulatory Care   
43684  02101810456  FL324054412PA2500XBLVD600    8130  Ambulatory Care   
43685  42201840354  NY112306719BR1958XAVEX300   21267   Health Related   
43686  04878020567  TX790705323PE3101XDRXX300   24534   Health Related   

            DATE STATE                         GOV_ADDR  \
0     2019-06-17    KY                  910 WALLACE AVE   
1     2019-09-17    IN              1141 HOSPITAL DR NW   
2     2019-06-17    KY                  910 WALLACE AVE   
3     2019-06-17    KY                  910 WALLACE AVE   
4     2021-02-18    KY                  910 WALLACE AVE   
...          ...   ...                              ...   
43682 2021-06-03    ID                  301 W MYRTLE ST   
43683 2021-06-03    FL  2500 MARTIN LUTHER KING JR BLVD   
43684 2021-06-03    FL  2500 MARTIN LUTHER KING JR BLVD   
43685 2021-06-13    NY                   1958 OCEAN AVE   
43686 2021-06-14    TX                  3101 GARRETT DR   

                             CRED_ADDR GOV_ZIP CRED_ZIP  
0                      910 Wallace Ave   42754    42754  
1                  1141 Hospital Dr NW   47112    47112  
2                      910 Wallace Ave   42754    42754  
3                      910 Wallace Ave   42754    42754  
4                      910 Wallace Ave   42754    42754  
...                                ...     ...      ...  
43682                  301 W Myrtle St   83702    83702  
43683  2500 Martin Luther King Jr Blvd   32405    32405  
43684  2500 Martin Luther King Jr Blvd   32405    32405  
43685                   1958 Ocean Ave   11230    11230  
43686                  3101 Garrett Dr   79070    79070  

[84778 rows x 10 columns]

In [144]:
ZIP_MATCHES = []
for row in check_12.itertuples():
    if row.GOV_ZIP != row.CRED_ZIP:
        ZIP_MATCH = True
    else:
        ZIP_MATCH = False
    ZIP_MATCHES.append(ZIP_MATCH)

In [145]:
check_12[ZIP_MATCHES].sort_values('DATE').drop_duplicates('ME',keep='last')

ME                    adrs_id  ORG_ID        CATEGORY  \
7296   03306000500  PA170428939LE283XXRDXX400    5689        Hospital   
18871  03601790482  OH447183602CA4665XNWXX400    5949  Health Related   
18870  49545800151  OH447183602CA4665XNWXX400    5949  Health Related   
21863  02701060396  MS395012515GU4500XSTXX300     472    Managed Care   
21864  02105091250  MS395012515GU4500XSTXX300     472    Managed Care   
...            ...                        ...     ...             ...   
23742  02879090418  MO634011257HAPOXXXBOXX201     213        Hospital   
2179   02604120961  NC277072325DU1301XSTXX300    3637        Hospital   
34221  02507931386  WI532263522MI9200XAVEX400     625        Hospital   
6949   02105800773  LA703014823TH602XXRDXX400    2286        Hospital   
39339  01222020146  GA317943648TI901XXEXXX400    1502        Hospital   

            DATE STATE              GOV_ADDR             CRED_ADDR GOV_ZIP  \
7296  2019-06-19    PA       283 S BUTLER RD         283 Butler Rd   17042   
18871 2019-06-27    OH     4665 BELPAR ST NW     4665 Belpar St NW   44718   
18870 2019-06-27    OH     4665 BELPAR ST NW     4665 Belpar St NW   44718   
21863 2019-07-01    MS          4500 13TH ST          4500 13th St   39501   
21864 2019-07-01    MS          4500 13TH ST          4500 13th St   39501   
...          ...   ...                   ...                   ...     ...   
23742 2021-06-14    MO                PO BOX           PO Box 1128   63401   
2179  2021-06-15    NC  1301 FAYETTEVILLE ST  1301 Fayetteville St   27707   
34221 2021-06-15    WI  9200 W WISCONSIN AVE  9000 W Wisconsin Ave   53226   
6949  2021-06-15    LA       602 N ACADIA RD       602 N Acadia Rd   70301   
39339 2021-06-15    GA         901 18TH ST E         901 E 18th St   31794   

      CRED_ZIP  
7296     17064  
18871    44735  
18870    44735  
21863    39502  
21864    39502  
...        ...  
23742    65102  
2179     27717  
34221    53201  
6949     70302  
39339    31793  

[712 rows x 10 columns]

In [149]:
this_is_it = check_12[130:]

In [227]:
check_12

ME                    adrs_id  ORG_ID  CATEGORY       DATE  \
1605   01611903177  IL627032403SP1025XSTXX400    2853     Group 2019-06-17   
6000   03901070627  OK741046520TU1923XAVEX401    1804  Hospital 2019-06-17   
5996   01902991120  OK741046520TU1923XAVEX401    1804  Hospital 2019-06-17   
5994   03901890586  OK741046520TU1923XAVEX401    1804  Hospital 2019-06-17   
5992   03901951011  OK741046520TU1923XAVEX401    1804  Hospital 2019-06-17   
...            ...                        ...     ...       ...        ...   
37397  03520790861  CT060692096SH50XXXRDXX400    3808  Hospital 2021-06-15   
37398  30813080334  CT060692096SH50XXXRDXX400    3808  Hospital 2021-06-15   
5544   49574030055  OH436082603TO2213XSTXX300    1527  Hospital 2021-06-15   
20809  91515070015  PA178379350LE1XXXXDRXX300      51  Hospital 2021-06-15   
20604  03901120756  CO807013290FO1000XSTXX311    2268  Hospital 2021-06-15   

      STATE             GOV_ADDR            CRED_ADDR GOV_ZIP CRED_ZIP  
1605     IL        1025 S 6TH ST        1025 S 6th St   62703    62703  
6000     OK     1923 S UTICA AVE     1923 S Utica Ave   74104    74104  
5996     OK     1923 S UTICA AVE     1923 S Utica Ave   74104    74104  
5994     OK     1923 S UTICA AVE     1923 S Utica Ave   74104    74104  
5992     OK     1923 S UTICA AVE     1923 S Utica Ave   74104    74104  
...     ...                  ...                  ...     ...      ...  
37397    CT  50 HOSPITAL HILL RD  50 Hospital Hill Rd   06069    06069  
37398    CT  50 HOSPITAL HILL RD  50 Hospital Hill Rd   06069    06069  
5544     OH       2213 CHERRY ST       2213 Cherry St   43608    43608  
20809    PA        1 HOSPITAL DR        1 Hospital Dr   17837    17837  
20604    CO      1000 LINCOLN ST      1000 Lincoln St   80701    80701  

[21253 rows x 10 columns]

In [151]:
this_is_it.columns

Index(['ME', 'adrs_id', 'ORG_ID', 'CATEGORY', 'DATE', 'STATE', 'GOV_ADDR',
       'CRED_ADDR', 'GOV_ZIP', 'CRED_ZIP'],
      dtype='object')

In [154]:
gov_phones = gov[['ME','adrs_id','phn_numbr']]

In [157]:
gov_phones.phn_numbr

4          5617377733.0
23         7344676770.0
25         5867774668.0
27         5089957800.0
28         9143663604.0
               ...     
2818914     7.13486e+09
2818915     2.03785e+09
2818916     6.19503e+09
2818917     6.19543e+09
2818918     8.58939e+09
Name: phn_numbr, Length: 2599175, dtype: object

In [159]:
my_phone = '7738993999'
my_phone[:10]

'7738993999'

In [165]:
gov_phones['TELEPHONE_NUMBER'] = [str(x).replace('.0','')[:10] for x in gov_phones.phn_numbr]

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [169]:
CREED = good_cred[['ADDRESS_LINE_1','ADDRESS_LINE_2','CITY','STATE','ZIPCODE','ORG_ID','ME']]

In [231]:
with_phones = pd.merge(check_12, yea, on=['ME','adrs_id']).drop_duplicates('ME', keep='last')

In [174]:
yea = gov_phones.drop_duplicates(['ME','TELEPHONE_NUMBER','adrs_id'])

In [222]:
check_12

ME                    adrs_id  ORG_ID         CATEGORY  \
982    04813150528  TX768018520BR1501XRDXX300    6592         Hospital   
1013   49583040055  MA023014042BR63XXXSTXX300    3938  Ambulatory Care   
7584   02106760171  OK741045336TU1784XAVEX400    1804         Hospital   
1604   01611903177  IL627032403SP1025XSTXX400    2853            Group   
7      49555850017  KY427542414LE910XXAVEX300    3588         Hospital   
...            ...                        ...     ...              ...   
4591   49550870141  CA960010852RE1100XSTXX300    2494         Hospital   
4636   04878101061  CA960010852RE1100XSTXX300    2494         Hospital   
49882  02105030501  MS392164500JA2500XSTXX400    2543         Hospital   
42129  04203010422  FL331334741MI3225XAVEX301   22416   Health Related   
25899  04102870480  MD214017901AN2002XPKWY306   10219  Ambulatory Care   

            DATE STATE           GOV_ADDR                  CRED_ADDR GOV_ZIP  \
982   2019-06-17    TX     1501 BURNET RD             1501 Burnet Rd   76801   
1013  2019-06-17    MA         63 MAIN ST                 63 Main St   02301   
7584  2019-06-17    OK   1784 S UTICA AVE           1923 S Utica Ave   74104   
1604  2019-06-17    IL      1025 S 6TH ST              1025 S 6th St   62703   
7     2019-06-17    KY    910 WALLACE AVE            910 Wallace Ave   42754   
...          ...   ...                ...                        ...     ...   
4591  2021-06-15    CA      1100 BUTTE ST              1100 Butte St   96001   
4636  2021-06-15    CA      1100 BUTTE ST              1100 Butte St   96001   
49882 2021-06-15    MS    2500 N STATE ST            1225 N State St   39216   
42129 2021-06-15    FL  3225 AVIATION AVE  3225 Aviation Ave Ste 700   33133   
25899 2021-06-15    MD  2002 MEDICAL PKWY  2002 Medical Pkwy Ste 330   21401   

      CRED_ZIP  
982      76801  
1013     02301  
7584     74104  
1604     62703  
7        42754  
...        ...  
4591     96001  
4636     96001  
49882    39202  
42129    33133  
25899    21401  

[23800 rows x 10 columns]

In [194]:
this_is_it

ME                    adrs_id  ORG_ID         CATEGORY  \
17202  44001930076  AL356304928FL1701XDRXX300     630         Hospital   
179    02106020674  LA711014644SH1500XAVEX302    3229         Hospital   
15462  03506060876  NY142630001BUELMXXSTXX400    3503         Hospital   
17701  70421920123  MI488672120OW826XXSTXX403    2542         Hospital   
17699  01104900212  MI488672120OW826XXSTXX403    2542         Hospital   
...            ...                        ...     ...              ...   
22561  02012890039  VA232351968RI8700XPKWY403    2190  Ambulatory Care   
22591  00802900741  VA232351968RI8700XPKWY403    2190  Ambulatory Care   
42129  04203010422  FL331334741MI3225XAVEX301   22416   Health Related   
5543   49574030055  OH436082603TO2213XSTXX300    1527         Hospital   
18186  01875990451  IN469471528LO1101XAVEX300    1647         Hospital   

            DATE STATE               GOV_ADDR                      CRED_ADDR  \
17202 2019-06-25    AL       1701 VETERANS DR              1701 Veterans Dr.   
179   2019-06-25    LA          1500 LINE AVE          1500 Line Ave Ste 206   
15462 2019-06-25    NY     ELM AND CARLTON ST        Elm and Carlton Streets   
17701 2019-06-25    MI          826 W KING ST                  826 W King St   
17699 2019-06-25    MI          826 W KING ST                  826 W King St   
...          ...   ...                    ...                            ...   
22561 2021-06-15    VA  8700 STONY POINT PKWY  8700 Stony Point Pkwy Ste 100   
22591 2021-06-15    VA  8700 STONY POINT PKWY  8700 Stony Point Pkwy Ste 100   
42129 2021-06-15    FL      3225 AVIATION AVE      3225 Aviation Ave Ste 700   
5543  2021-06-15    OH         2213 CHERRY ST                 2213 Cherry St   
18186 2021-06-15    IN      1101 MICHIGAN AVE              1101 Michigan Ave   

      GOV_ZIP CRED_ZIP  
17202   35630    35630  
179     71101    71101  
15462   14263    14263  
17701   48867    48867  
17699   48867    48867  
...       ...      ...  
22561   23235    23235  
22591   23235    23235  
42129   33133    33133  
5543    43608    43608  
18186   46947    46947  

[20000 rows x 10 columns]

In [195]:
CREED

ADDRESS_LINE_1        ADDRESS_LINE_2               CITY STATE  \
113758         910 Wallace Ave                  None        Leitchfield    KY   
444247        4800 Belfort Rd.                  None       Jacksonville    FL   
444252        4800 Belfort Rd.                  None       Jacksonville    FL   
444256        4800 Belfort Rd.                  None       Jacksonville    FL   
444257        4800 Belfort Rd.                  None       Jacksonville    FL   
...                        ...                   ...                ...   ...   
623043        800 W Central Rd                  None  Arlington Heights    IL   
371197            Medical Arts  836 E 65th St Ste 20           Savannah    GA   
419283            1 Perkins Sq                  None              Akron    OH   
201092    200 Corporate Blvd S                  None            Yonkers    NY   
314593  130 Desiard St Ste 300                  None             Monroe    LA   

          ZIPCODE  ORG_ID           ME  
113758  427542414    3588  02002061344  
444247      32256    2202  02105021278  
444252      32256    2202  03841040561  
444256      32256    2202  01175990140  
444257      32256    2202  02834821462  
...           ...     ...          ...  
623043  600052349    4917  01611182879  
371197      31405     340  01222920252  
419283  443081062    1906  04177080956  
201092  107016806     725  87501110408  
314593  712017363     139  30501060760  

[301480 rows x 7 columns]

In [196]:
gov_phones

ME                    adrs_id     phn_numbr TELEPHONE_NUMBER
4        91504890100  FL334357995BO2815XBLVD400  5617377733.0       5617377733
23       70425930077  MI481842405WA33101STXX300  7344676770.0       7344676770
25       70425930077  MI480664473RO25250RDXX301  5867774668.0       5867774668
27       03305740925  MA027476244DA299XXRDXX401  5089957800.0       5089957800
28       03508712188  NY105911020SL701XXBROA300  9143663604.0       9143663604
...              ...                        ...           ...              ...
2818914  65401151774  TX770815333HO5420XDRXX302   7.13486e+09       7134862900
2818915  04115120323  CT065048901NE1XXXXSTXX300   2.03785e+09       2037854081
2818916  70402110081  CA919116617CH751XXCTXX400   6.19503e+09       6195025800
2818917  70402110081  CA921154637SA4940XBLVD400   6.19543e+09       6195434500
2818918  70402110081  CA921232701SA7901XSTXX300   8.58939e+09       8589393400

[2599175 rows x 4 columns]

In [202]:
with_phone = pd.merge(this_is_it, gov_phones, on=['ME', 'adrs_id']).drop_duplicates('ME')

In [232]:
YESS = pd.merge(with_phones, CREED, on=['ORG_ID', 'ME']).drop_duplicates('ME')

In [207]:
YESS.columns

Index(['ME', 'adrs_id', 'ORG_ID', 'CATEGORY', 'DATE', 'STATE_x', 'GOV_ADDR',
       'CRED_ADDR', 'GOV_ZIP', 'CRED_ZIP', 'phn_numbr', 'TELEPHONE_NUMBER',
       'ADDRESS_LINE_1', 'ADDRESS_LINE_2', 'CITY', 'STATE_y', 'ZIPCODE'],
      dtype='object')

In [254]:
COLS = {'STATE_y':'POLO_STATE','ADDRESS_LINE_1':'POLO_MAILING_LINE_2','ADDRESS_LINE_2':'POLO_MAILING_LINE_1','CITY':'POLO_CITY', 'description':'DESCRIPTION'}

In [233]:
mwah = pd.merge(ppd[['ME','FIRST_NAME','MIDDLE_NAME','LAST_NAME','SUFFIX','PRIM_SPEC_CD','PE_CD','FAX_NUMBER','TOP_CD']], YESS, on='ME')
pe_cd = pd.read_excel('../../Data/AMAIA/PRESENT_EMPLOYMENT_CODE_KEY.xlsx')
mwah = pd.merge(mwah, pe_cd, left_on='PE_CD', right_on='present_emp_cd', how='left')

In [237]:
unos = mwah.drop_duplicates('TELEPHONE_NUMBER', keep=False)

In [260]:
bah = mwah[mwah.ME.isin(unos.ME)==False].sort_values('DATE', ascending=False)[:17799]

In [239]:
unos

ME FIRST_NAME MIDDLE_NAME       LAST_NAME SUFFIX PRIM_SPEC_CD  \
12     00102020065     ROBERT       DAVID     KACHELHOFER   None           DR   
15     00102020600       JEFF        None      CHAIPRAKOB   None          OPH   
19     00102021461      KEITH        ERIC          GIPSON   None           AN   
20     00102030079      BRIAN        NEIL       VALENTINE   None           DR   
23     00102030648   BEATRICE        None  CHAICHARNCHEEP   None           GS   
...            ...        ...         ...             ...    ...          ...   
21177  94101720432       NGOC           T          NGUYEN   None           GP   
21179  94201010050        HAU         VAN            TRAN   None           FM   
21186  95701940068       DINO           D        KLISOVIC   None          OPH   
21187  95701960018     ZDENKO        None         KORUNDA   None          PMM   
21193  95702750017     MILENA        None     JANICIJEVIC   None           AN   

       PE_CD   FAX_NUMBER  TOP_CD                    adrs_id  ...  CRED_ZIP  \
12        30  2.05482e+09      20  AL350224527BE995XXSWXX400  ...     35022   
15       110         None      20  AL352353422BI52XXXDRXX401  ...     35235   
19        30         None      20  MA011071179SP100XXAVEX309  ...     01107   
20        30         None      20  AL359031195GA1007XAVEX300  ...     35903   
23       110         None      20  AL350224527BE995XXSWXX400  ...     35022   
...      ...          ...     ...                        ...  ...       ...   
21177     13  7.14531e+09      72  CA928431834GR12302BLVD401  ...     92843   
21179     50         None      12  MO646282337BR130XXAVEX401  ...     64628   
21186     30   6.1434e+09      20  OH456012526CH159XXSTXX400  ...     45601   
21187     30  2.39595e+09      20  FL341193900NA6101XRDXX400  ...     34119   
21193     30   7.2443e+09      20  PA154015514UN500XXSTXX400  ...     15401   

          phn_numbr TELEPHONE_NUMBER                ADDRESS_LINE_1  \
12     2054817155.0       2054817155                995 9th Ave SW   
15     2058383696.0       2058383696  52 Medical Park Dr E Ste 305   
19     4133042171.0       4133042171         100 Wason Ave Ste 110   
20     2564944033.0       2564944033             1007 Goodyear Ave   
23     2054818790.0       2054818790                995 9th Ave SW   
...             ...              ...                           ...   
21177  7145302772.0       7145302772       12601 Garden Grove Blvd   
21179  6602581283.0       6602581283             130 E Lockling St   
21186  6143398500.0       6143398500                  159 E 2nd St   
21187  2395912803.0       2395912803            6101 Pine Ridge Rd   
21193  7244305000.0       7244305000             500 W Berkeley St   

      ADDRESS_LINE_2          CITY STATE_y    ZIPCODE present_emp_cd  \
12              None      Bessemer      AL  350224527             30   
15              None    Birmingham      AL  352353409            110   
19              None   Springfield      MA  011071198             30   
20              None       Gadsden      AL  359031100             30   
23              None      Bessemer      AL  350224527            110   
...              ...           ...     ...        ...            ...   
21177           None  Garden Grove      CA  928431908             13   
21179           None    Brookfield      MO  646282337             50   
21186           None   Chillicothe      OH  456012526             30   
21187           None        Naples      FL  341193900             30   
21193           None     Uniontown      PA  154015596             30   

                                     description  
12                                Group Practice  
15                             No Classification  
19                                Group Practice  
20                                Group Practice  
23                             No Classification  
...                                          ...  
21177  Two Physician Practice-F

In [259]:
20000-2201

17799

In [242]:
mwah.columns

Index(['ME', 'FIRST_NAME', 'MIDDLE_NAME', 'LAST_NAME', 'SUFFIX',
       'PRIM_SPEC_CD', 'PE_CD', 'FAX_NUMBER', 'TOP_CD', 'adrs_id', 'ORG_ID',
       'CATEGORY', 'DATE', 'STATE_x', 'GOV_ADDR', 'CRED_ADDR', 'GOV_ZIP',
       'CRED_ZIP', 'phn_numbr', 'TELEPHONE_NUMBER', 'ADDRESS_LINE_1',
       'ADDRESS_LINE_2', 'CITY', 'STATE_y', 'ZIPCODE', 'present_emp_cd',
       'description'],
      dtype='object')

In [261]:
the_end = pd.concat([unos, bah])

In [262]:
the_end['POLO_ZIP'] = [use.fix_zipcode(x) for x in the_end.ZIPCODE]

In [263]:
the_end = the_end.rename(columns=COLS)

In [264]:
the_end

ME FIRST_NAME MIDDLE_NAME        LAST_NAME SUFFIX  \
12     00102020065     ROBERT       DAVID      KACHELHOFER   None   
15     00102020600       JEFF        None       CHAIPRAKOB   None   
19     00102021461      KEITH        ERIC           GIPSON   None   
20     00102030079      BRIAN        NEIL        VALENTINE   None   
23     00102030648   BEATRICE        None   CHAICHARNCHEEP   None   
...            ...        ...         ...              ...    ...   
3253   01642050288       LISA        ANNE          HOPKINS   None   
19134  64902040071      KARLA        None  TREVINO RAMIREZ   None   
4388   01902080585   CLAYBORN        JOHN           MORRIS   None   
543    00506780071      DAREL        JOHN        BENVENUTI   None   
3113   01611860591    WILLIAM       DAVID          DACHMAN   None   

      PRIM_SPEC_CD  PE_CD   FAX_NUMBER  TOP_CD                    adrs_id  \
12              DR     30  2.05482e+09      20  AL350224527BE995XXSWXX400   
15             OPH    110         None      20  AL352353422BI52XXXDRXX401   
19              AN     30         None      20  MA011071179SP100XXAVEX309   
20              DR     30         None      20  AL359031195GA1007XAVEX300   
23              GS    110         None      20  AL350224527BE995XXSWXX400   
...            ...    ...          ...     ...                        ...   
3253            GS     30  7.32846e+09      20  NJ089011723NE240XXAVEX304   
19134           FM     30         None      20  TX785399152ED5501XRDXX400   
4388            EM     50         None      20  IL606081782CH1500XAVEX400   
543             CD     30   9.4965e+09      20  CA926634162NE1XXXXDRXX300   
3113            PA     30  6.02344e+09      20  AZ850084973PH2601XSTXX400   

       ...     phn_numbr TELEPHONE_NUMBER           POLO_MAILING_LINE_2  \
12     ...  2054817155.0       2054817155                995 9th Ave SW   
15     ...  2058383696.0       2058383696  52 Medical Park Dr E Ste 305   
19     ...  4133042171.0       4133042171         100 Wason Ave Ste 110   
20     ...  2564944033.0       2564944033             1007 Goodyear Ave   
23     ...  2054818790.0       2054818790                995 9th Ave SW   
...    ...           ...              ...                           ...   
3253   ...  7325655453.0       7325655453                240 Easton Ave   
19134  ...  9563628677.0       9563628677              5501 S McColl Rd   
4388   ...  7735422000.0       7735422000          1500 S Fairfield Ave   
543    ...  9497605856.0       9497605856                     1 Hoag Dr   
3113   ...  6023441015.0       6023441015           2601 E Roosevelt St   

      POLO_MAILING_LINE_1      POLO_CITY POLO_STATE    ZIPCODE present_emp_cd  \
12                   None       Bessemer         AL  350224527             30   
15                   None     Birmingham         AL  352353409            110   
19                   None    Springfield         MA  011071198             30   
20                   None        Gadsden         AL  359031100             30   
23                   None       Bessemer         AL  350224527            110   
...                   ...            ...        ...        ...            ...   
3253                 None  New Brunswick         NJ  089011723             30   
19134                None       Edinburg         TX  785399152             30   
4388                 None        Chicago         IL  606081782             50   
543                  None  Newport Beach         CA  926634162             30   
3113                 None        Phoenix         AZ  850084973             30   

                   DESCRIPTION POLO_ZIP  
12              Group Practice    35022  
15           No Classification    35235  
19              Group Practice    01107  
20              Group Practice    35903  
23           No Classification    35022  
...                        ...      ...  
3253            Group Practice    08901  
19134           Group Practice    78539  
4388   Non

In [265]:
the_end[['ME',
 'FIRST_NAME',
 'MIDDLE_NAME',
 'LAST_NAME',
 'SUFFIX',
 'POLO_MAILING_LINE_1',
 'POLO_MAILING_LINE_2',
 'POLO_CITY',
 'POLO_STATE',
 'POLO_ZIP',
 'TELEPHONE_NUMBER',
 'PRIM_SPEC_CD',
 'DESCRIPTION',
 'PE_CD',
 'FAX_NUMBER']].to_excel('../../Data/Credentialling/Profile_Order_Humach_Sample_2021-06-22.xlsx', index=False)

In [266]:
the_end.to_csv('../../Data/Credentialling/Profile_Orders_2021-06-22.xlsx', index=False)

In [19]:
def fix_phone(num):
    num = str(num).strip().replace('.0', '')
    if num[0] == '1':
        num = num[1:]
    num = ''.join(filter(str.isdigit, num))
    num = num[:10]
    return num

In [22]:
fix_phone('1.773.239.5590')

'7732395590'